### Imports

In [50]:
import struct
import os
from scipy.optimize import curve_fit
from mpl_toolkits.mplot3d import Axes3D
import plotly.io as pio # themes
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()
import numpy as np
import pandas as pd

idx = pd.IndexSlice
bgcolour = "rgb(15, 23, 42)"
plotly_template = pio.templates["plotly_dark"]

### Reading & unpacking the binary data file

This code first constructs the path to the out folder for the specific simulation run. It then uses os.listdir to get a list of filenames in the out folder, and filters the list to only include filenames that end with ".bin". The resulting list of snapshot filenames is then sorted, so that the snapshots are processed in order.

In [51]:
simulation_run_folder = "2023-02-12--22-54-11"# "2023-02-12--16-00-00"
snapshot_folder = os.path.join("out", simulation_run_folder)

snapshot_filenames = []
for filename in os.listdir(snapshot_folder):
    if filename.endswith(".bin"):
        snapshot_filenames.append(os.path.join(snapshot_folder, filename))

snapshot_filenames.sort()

#### - Reading the header data

This function reads the header data from the binary file - in most cases, we only need to read the first snapshot, since the header data is the same for all snapshots. 

In [52]:
def read_header(filename):
    with open(filename, 'rb') as f:
        header_dtype = np.dtype([('N', np.int32),
                                ('timestep', np.float32),
                                ('softening_factor', np.float32),
                                ('total_iterations', np.int32),
                                ('snapshot_interval', np.int32),])
        
        header = np.frombuffer(f.read(header_dtype.itemsize), header_dtype)

    n_bodies = header['N'][0]
    timestep = header['timestep'][0]
    softening_factor = header['softening_factor'][0]
    total_iterations = header['total_iterations'][0]
    snapshot_interval = header['snapshot_interval'][0]
    total_snapshots = len(snapshot_filenames) # (total_iterations // snapshot_interval)

    return n_bodies, timestep, softening_factor, total_iterations, snapshot_interval, total_snapshots

Now, we extract the header data and store them in their own variables.

In [53]:
n_bodies, timestep, softening_factor, total_iterations, snapshot_interval, total_snapshots = read_header(snapshot_filenames[0])

print("N: ", n_bodies)
print("timestep: ", timestep, "days")
print("total_iterations: ", total_iterations)
print("snapshot_interval: ", snapshot_interval)
print("softening_factor: ", softening_factor)
print("total_snapshots: ", total_snapshots)

N:  10
timestep:  10.0 days
total_iterations:  1000000
snapshot_interval:  10000
softening_factor:  0.000125
total_snapshots:  100


#### - Reading the snapshot data

This function reads each binary snapshot file in turn using `np.frombuffer`, and returns the data as a numpy array.

In [54]:
def read_snapshots():

    mass = np.zeros((total_iterations, n_bodies), dtype=np.float32)
    pos = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)
    vel = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)
    acc = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)

    dt_bytes = n_bodies * 10 * 4
    iteration = 0

    for snapshot_filename in snapshot_filenames:
        with open(snapshot_filename, "rb") as f:
            f.seek(5 * 4) # Skip the header (20 bytes)

            for i in range(0, snapshot_interval):
                # Read the binary data into a numpy array
                snapshot = np.frombuffer(f.read(dt_bytes), dtype=np.float32)
                
                # Reshape the array to the correct dimensions
                snapshot = snapshot.reshape((n_bodies, 10))

                # Extract the mass, position (x, y, z), velocity (x, y, z), and force (x, y, z) at current timestep
                mass[iteration, :] = snapshot[:, 0]
                pos[iteration, :, :] = snapshot[:, 1:4]
                vel[iteration, :, :] = snapshot[:, 4:7]
                acc[iteration, :, :] = snapshot[:, 7:10]

                iteration += 1

    return mass, pos, vel, acc

#### - Data extraction guide

- mass => `mass[i, :]`   - mass of each particle in the snapshot
- pos  => `pos[i, :, :]` - position of each particle in the snapshot
    - x => `pos[i, :, 0]` - x position
    - y => `pos[i, :, 1]` - y position
    - z => `pos[i, :, 2]` - z position
- vel  => `vel[i, :, :]` - velocity of each particle in the snapshot
    - vx => `vel[i, :, 0]` - x velocity
    - vy => `vel[i, :, 1]` - y velocity
    - vz => `vel[i, :, 2]` - z velocity
- acc  => `acc[i, :, :]` - acceleration of each particle in the snapshot
    - ax => `acc[i, :, 0]` - x acceleration
    - ay => `acc[i, :, 1]` - y acceleration
    - az => `acc[i, :, 2]` - z acceleration

... except data manipulation is easier and faster if we pack the data into a dataframe, so we'll do that instead.

Extracting data into individual dataframes

In [55]:
mass, pos, vel, acc = read_snapshots()

x = pos[:, :, 0]
y = pos[:, :, 1]
z = pos[:, :, 2]
vx = vel[:, :, 0]
vy = vel[:, :, 1]
vz = vel[:, :, 2]
fx = acc[:, :, 0]
fy = acc[:, :, 1]
fz = acc[:, :, 2]

df_list = []
for i in range(n_bodies):
    data = {
        "mass": mass[:, i],
        "x": x[:, i],
        "y": y[:, i],
        "z": z[:, i],
        "vx": vx[:, i],
        "vy": vy[:, i],
        "vz": vz[:, i],
        "fx": fx[:, i],
        "fy": fy[:, i],
        "fz": fz[:, i],
    }
    df_list.append(pd.DataFrame(data))

df = pd.concat(df_list, axis=1, keys=["{}".format(i) for i in range(n_bodies)])

mass = df.loc[:,idx[:,'mass']]
x = df.loc[:,idx[:,'x']] # .groupby(level=0, axis=1).sum()
y = df.loc[:,idx[:,'y']]
z = df.loc[:,idx[:,'z']]

fx = df.loc[:,idx[:,'fx']]
fy = df.loc[:,idx[:,'fy']]
fz = df.loc[:,idx[:,'fz']]

vx = df.loc[:,idx[:,'vx']]
vy = df.loc[:,idx[:,'vy']]
vz = df.loc[:,idx[:,'vz']]

### Plotting the data

In [56]:
print(df[f'0']['x'])

0         1626.728516
1         1626.729126
2         1626.729736
3         1626.730347
4         1626.730957
             ...     
999995    -628.182678
999996    -628.177307
999997    -628.171936
999998    -628.166565
999999    -628.161194
Name: x, Length: 1000000, dtype: float32


In [57]:
test = x.groupby(level=0, axis=1).sum()
print(test.loc[1])

0    1626.729126
1    1201.319946
2    1202.309448
3    3091.427490
4    1200.017700
5    1946.964600
6    2788.621582
7    2711.666748
8    2521.471680
9    2736.593506
Name: 1, dtype: float32


In [58]:
# print(df[::2])
# print x position for each body every 100 timesteps
# print(df.loc[::100, idx[:, 'x']])
# print x position for body i every 100 timesteps
i=4
print(df.loc[::100, idx[f'{i}', 'x']])

0         1200.018433
100       1199.947021
200       1199.885986
300       1199.824951
400       1199.763916
             ...     
999500    -488.117981
999600    -487.957916
999700    -487.773865
999800    -487.566223
999900    -487.335144
Name: (4, x), Length: 10000, dtype: float32


In [63]:
# Dataset
iteration_step = 100
data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']], 
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']], 
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
                    for i in range(n_bodies)]

# Layout
zoom = 1.2

layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom)
        ),
    xaxis=dict(
        showgrid=False,
    ),
    yaxis=dict(
        showgrid=False,
    ),
)
    
fig = go.Figure(data=data, layout=layout)
fig.update_layout(template=plotly_template)
fig.show()

In [60]:
# # Dataset
# data=[go.Scatter3d(x=df[f'{i}']['x'], 
#                     y=df[f'{i}']['y'], 
#                     z=df[f'{i}']['z'],
#                     mode='lines',
#                     name=f'Body {i}',
#                     line=dict(
#                         width=2*df[f'{i}']['mass'][0],
#                         colorscale='Viridis'
#                         ))
#                     # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
#                     for i in range(n_bodies)]

# # Layout
# zoom = 1.2

# layout = go.Layout(
#     title='N-Body Simulation',
#     autosize=False,
#     height=900,
#     width=1400,
#     scene=dict(
#         aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom)
#         ),
# )
    
# fig = go.Figure(data=data, layout=layout)
# fig.update_layout(template=plotly_template)
# fig.show()



KeyboardInterrupt: 